In [1]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import plotly.express as px
import seaborn as sns
import warnings
warnings.filterwarnings('ignore')
from sklearn.model_selection import train_test_split as holdout
from plotly.offline import init_notebook_mode, iplot
init_notebook_mode(connected=True)
from sklearn.linear_model import LinearRegression
from sklearn import metrics
from sklearn.neighbors import KNeighborsRegressor
from sklearn.tree import DecisionTreeRegressor
from sklearn.ensemble import RandomForestRegressor
from sklearn.svm import SVR 
from sklearn.metrics import mean_absolute_error, mean_squared_error, accuracy_score
from sklearn.model_selection import train_test_split 
from sklearn.preprocessing import Normalizer, StandardScaler, MinMaxScaler
from sklearn.impute import SimpleImputer
from sklearn.preprocessing import RobustScaler

In [2]:
df=pd.read_csv("Temperature_Forecast.csv")
df

station        Date  Present_Tmax  Present_Tmin  LDAPS_RHmin  \
0         1.0  30-06-2013          28.7          21.4    58.255688   
1         2.0  30-06-2013          31.9          21.6    52.263397   
2         3.0  30-06-2013          31.6          23.3    48.690479   
3         4.0  30-06-2013          32.0          23.4    58.239788   
4         5.0  30-06-2013          31.4          21.9    56.174095   
...       ...         ...           ...           ...          ...   
7747     23.0  30-08-2017          23.3          17.1    26.741310   
7748     24.0  30-08-2017          23.3          17.7    24.040634   
7749     25.0  30-08-2017          23.2          17.4    22.933014   
7750      NaN         NaN          20.0          11.3    19.794666   
7751      NaN         NaN          37.6          29.9    98.524734   

      LDAPS_RHmax  LDAPS_Tmax_lapse  LDAPS_Tmin_lapse   LDAPS_WS    LDAPS_LH  \
0       91.116364         28.074101         23.006936   6.818887   69.451805   
1       90.604721         29.850689         24.035009   5.691890   51.937448   
2       83.973587         30.091292         24.565633   6.138224   20.573050   
3       96.483688         29.704629         23.326177   5.650050   65.727144   
4       90.155128         29.113934         23.486480   5.735004  107.965535   
...           ...               ...               ...        ...         ...   
7747    78.869858         26.352081         18.775678   6.148918   72.058294   
7748    77.294975         27.010193         18.733519   6.542819   47.241457   
7749    77.243744         27.939516         18.522965   7.289264    9.090034   
7750    58.936283         17.624954         14.272646   2.882580  -13.603212   
7751   100.000153         38.542255         29.619342  21.857621  213.414006   

      ...  LDAPS_PPT2  LDAPS_PPT3  LDAPS_PPT4      lat      lon       DEM  \
0     ...    0.000000    0.000000    0.000000  37.6046  126.991  212.3350   
1     ...    0.000000    0.000000    0.000000  37.6046  127.032   44.7624   
2     ...    0.000000    0.000000    0.000000  37.5776  127.058   33.3068   
3     ...    0.000000    0.000000    0.000000  37.6450  127.022   45.7160   
4     ...    0.000000    0.000000    0.000000  37.5507  127.135   35.0380   
...   ...         ...         ...         ...      ...      ...       ...   
7747  ...    0.000000    0.000000    0.000000  37.5372  126.891   15.5876   
7748  ...    0.000000    0.000000    0.000000  37.5237  126.909   17.2956   
7749  ...    0.000000    0.000000    0.000000  37.5237  126.970   19.5844   
7750  ...    0.000000    0.000000    0.000000  37.4562  126.826   12.3700   
7751  ...   21.621661   15.841235   16.655469  37.6450  127.135  212.3350   

         Slope  Solar radiation  Next_Tmax  Next_Tmin  
0     2.785000      5992.895996       29.1       21.2  
1     0.514100      5869.312500       30.5       22.5  
2     0.266100      5863.555664       31.1       23.9  
3     2.534800      5856.964844       31.7       24.3  
4     0.505500      5859.552246       31.2       22.5  
...        ...              ...        ...        ...  
7747  0.155400      4443.313965       28.3       18.1  
7748  0.222300      4438.373535       28.6       18.8  
7749  0.271300      4451.345215       27.8       17.4  
7750  0.098475      4329.520508       17.4       11.3  
7751  5.178230      5992.895996       38.9       29.8  

[7752 rows x 25 columns]

In [3]:
temp=df.copy()

In [4]:
temp.isnull().sum()


station              2
Date                 2
Present_Tmax        70
Present_Tmin        70
LDAPS_RHmin         75
LDAPS_RHmax         75
LDAPS_Tmax_lapse    75
LDAPS_Tmin_lapse    75
LDAPS_WS            75
LDAPS_LH            75
LDAPS_CC1           75
LDAPS_CC2           75
LDAPS_CC3           75
LDAPS_CC4           75
LDAPS_PPT1          75
LDAPS_PPT2          75
LDAPS_PPT3          75
LDAPS_PPT4          75
lat                  0
lon                  0
DEM                  0
Slope                0
Solar radiation      0
Next_Tmax           27
Next_Tmin           27
dtype: int64

In [5]:
temp.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 7752 entries, 0 to 7751
Data columns (total 25 columns):
 #   Column            Non-Null Count  Dtype  
---  ------            --------------  -----  
 0   station           7750 non-null   float64
 1   Date              7750 non-null   object 
 2   Present_Tmax      7682 non-null   float64
 3   Present_Tmin      7682 non-null   float64
 4   LDAPS_RHmin       7677 non-null   float64
 5   LDAPS_RHmax       7677 non-null   float64
 6   LDAPS_Tmax_lapse  7677 non-null   float64
 7   LDAPS_Tmin_lapse  7677 non-null   float64
 8   LDAPS_WS          7677 non-null   float64
 9   LDAPS_LH          7677 non-null   float64
 10  LDAPS_CC1         7677 non-null   float64
 11  LDAPS_CC2         7677 non-null   float64
 12  LDAPS_CC3         7677 non-null   float64
 13  LDAPS_CC4         7677 non-null   float64
 14  LDAPS_PPT1        7677 non-null   float64
 15  LDAPS_PPT2        7677 non-null   float64
 16  LDAPS_PPT3        7677 non-null   float64


In [6]:
temp.head()

station        Date  Present_Tmax  Present_Tmin  LDAPS_RHmin  LDAPS_RHmax  \
0      1.0  30-06-2013          28.7          21.4    58.255688    91.116364   
1      2.0  30-06-2013          31.9          21.6    52.263397    90.604721   
2      3.0  30-06-2013          31.6          23.3    48.690479    83.973587   
3      4.0  30-06-2013          32.0          23.4    58.239788    96.483688   
4      5.0  30-06-2013          31.4          21.9    56.174095    90.155128   

   LDAPS_Tmax_lapse  LDAPS_Tmin_lapse  LDAPS_WS    LDAPS_LH  ...  LDAPS_PPT2  \
0         28.074101         23.006936  6.818887   69.451805  ...         0.0   
1         29.850689         24.035009  5.691890   51.937448  ...         0.0   
2         30.091292         24.565633  6.138224   20.573050  ...         0.0   
3         29.704629         23.326177  5.650050   65.727144  ...         0.0   
4         29.113934         23.486480  5.735004  107.965535  ...         0.0   

   LDAPS_PPT3  LDAPS_PPT4      lat      lon       DEM   Slope  \
0         0.0         0.0  37.6046  126.991  212.3350  2.7850   
1         0.0         0.0  37.6046  127.032   44.7624  0.5141   
2         0.0         0.0  37.5776  127.058   33.3068  0.2661   
3         0.0         0.0  37.6450  127.022   45.7160  2.5348   
4         0.0         0.0  37.5507  127.135   35.0380  0.5055   

   Solar radiation  Next_Tmax  Next_Tmin  
0      5992.895996       29.1       21.2  
1      5869.312500       30.5       22.5  
2      5863.555664       31.1       23.9  
3      5856.964844       31.7       24.3  
4      5859.552246       31.2       22.5  

[5 rows x 25 columns]

In [7]:
temp.shape

(7752, 25)

In [8]:
temp.describe()

station  Present_Tmax  Present_Tmin  LDAPS_RHmin  LDAPS_RHmax  \
count  7750.000000   7682.000000   7682.000000  7677.000000  7677.000000   
mean     13.000000     29.768211     23.225059    56.759372    88.374804   
std       7.211568      2.969999      2.413961    14.668111     7.192004   
min       1.000000     20.000000     11.300000    19.794666    58.936283   
25%       7.000000     27.800000     21.700000    45.963543    84.222862   
50%      13.000000     29.900000     23.400000    55.039024    89.793480   
75%      19.000000     32.000000     24.900000    67.190056    93.743629   
max      25.000000     37.600000     29.900000    98.524734   100.000153   

       LDAPS_Tmax_lapse  LDAPS_Tmin_lapse     LDAPS_WS     LDAPS_LH  \
count       7677.000000       7677.000000  7677.000000  7677.000000   
mean          29.613447         23.512589     7.097875    62.505019   
std            2.947191          2.345347     2.183836    33.730589   
min           17.624954         14.272646     2.882580   -13.603212   
25%           27.673499         22.089739     5.678705    37.266753   
50%           29.703426         23.760199     6.547470    56.865482   
75%           31.710450         25.152909     8.032276    84.223616   
max           38.542255         29.619342    21.857621   213.414006   

         LDAPS_CC1  ...   LDAPS_PPT2   LDAPS_PPT3   LDAPS_PPT4          lat  \
count  7677.000000  ...  7677.000000  7677.000000  7677.000000  7752.000000   
mean      0.368774  ...     0.485003     0.278200     0.269407    37.544722   
std       0.262458  ...     1.762807     1.161809     1.206214     0.050352   
min       0.000000  ...     0.000000     0.000000     0.000000    37.456200   
25%       0.146654  ...     0.000000     0.000000     0.000000    37.510200   
50%       0.315697  ...     0.000000     0.000000     0.000000    37.550700   
75%       0.575489  ...     0.018364     0.007896     0.000041    37.577600   
max       0.967277  ...    21.621661    15.841235    16.655469    37.645000   

               lon          DEM        Slope  Solar radiation    Next_Tmax  \
count  7752.000000  7752.000000  7752.000000      7752.000000  7725.000000   
mean    126.991397    61.867972     1.257048      5341.502803    30.274887   
std       0.079435    54.279780     1.370444       429.158867     3.128010   
min     126.826000    12.370000     0.098475      4329.520508    17.400000   
25%     126.937000    28.700000     0.271300      4999.018555    28.200000   
50%     126.995000    45.716000     0.618000      5436.345215    30.500000   
75%     127.042000    59.832400     1.767800      5728.316406    32.600000   
max     127.135000   212.335000     5.178230      5992.895996    38.900000   

         Next_Tmin  
count  7725.000000  
mean     22.932220  
std       2.487613  
min      11.300000  
25%      21.300000  
50%      23.100000  
75%      24.600000  
max      29.800000  

[8 rows x 24 columns]

In [9]:
temp.skew()

station             0.000000
Present_Tmax       -0.262942
Present_Tmin       -0.365875
LDAPS_RHmin         0.298765
LDAPS_RHmax        -0.850870
LDAPS_Tmax_lapse   -0.226775
LDAPS_Tmin_lapse   -0.578943
LDAPS_WS            1.571581
LDAPS_LH            0.670491
LDAPS_CC1           0.457231
LDAPS_CC2           0.470060
LDAPS_CC3           0.637630
LDAPS_CC4           0.663251
LDAPS_PPT1          5.367675
LDAPS_PPT2          5.747360
LDAPS_PPT3          6.425829
LDAPS_PPT4          6.792379
lat                 0.087062
lon                -0.285213
DEM                 1.723257
Slope               1.563020
Solar radiation    -0.511210
Next_Tmax          -0.339607
Next_Tmin          -0.403743
dtype: float64

In [10]:
temp['Date'][0].split('-')

['30', '06', '2013']

In [11]:
list_of_year = [ ]
list_of_month = [ ]
list_of_day = [ ]

for i in temp['Date']:
    try :
        split_obj = i.split('-')
        list_of_year.append(split_obj[2])
        list_of_month.append(split_obj[1])    
        list_of_day.append(split_obj[0]) 
    except AttributeError:
        list_of_year.append(np.nan)
        list_of_month.append(np.nan)
        list_of_day.append(np.nan)

In [12]:
temp['year'] = list_of_year
temp['month'] = list_of_month
temp['day'] = list_of_day

In [13]:
temp['year'] = pd.to_numeric(temp['year']) 
temp['month'] = pd.to_numeric(temp['month']) 
temp['day'] = pd.to_numeric(temp['day'])

In [14]:
temp.drop('Date', axis=1, inplace=True)

In [15]:
temp

station  Present_Tmax  Present_Tmin  LDAPS_RHmin  LDAPS_RHmax  \
0         1.0          28.7          21.4    58.255688    91.116364   
1         2.0          31.9          21.6    52.263397    90.604721   
2         3.0          31.6          23.3    48.690479    83.973587   
3         4.0          32.0          23.4    58.239788    96.483688   
4         5.0          31.4          21.9    56.174095    90.155128   
...       ...           ...           ...          ...          ...   
7747     23.0          23.3          17.1    26.741310    78.869858   
7748     24.0          23.3          17.7    24.040634    77.294975   
7749     25.0          23.2          17.4    22.933014    77.243744   
7750      NaN          20.0          11.3    19.794666    58.936283   
7751      NaN          37.6          29.9    98.524734   100.000153   

      LDAPS_Tmax_lapse  LDAPS_Tmin_lapse   LDAPS_WS    LDAPS_LH  LDAPS_CC1  \
0            28.074101         23.006936   6.818887   69.451805   0.233947   
1            29.850689         24.035009   5.691890   51.937448   0.225508   
2            30.091292         24.565633   6.138224   20.573050   0.209344   
3            29.704629         23.326177   5.650050   65.727144   0.216372   
4            29.113934         23.486480   5.735004  107.965535   0.151407   
...                ...               ...        ...         ...        ...   
7747         26.352081         18.775678   6.148918   72.058294   0.030034   
7748         27.010193         18.733519   6.542819   47.241457   0.035874   
7749         27.939516         18.522965   7.289264    9.090034   0.048954   
7750         17.624954         14.272646   2.882580  -13.603212   0.000000   
7751         38.542255         29.619342  21.857621  213.414006   0.967277   

      ...      lat      lon       DEM     Slope  Solar radiation  Next_Tmax  \
0     ...  37.6046  126.991  212.3350  2.785000      5992.895996       29.1   
1     ...  37.6046  127.032   44.7624  0.514100      5869.312500       30.5   
2     ...  37.5776  127.058   33.3068  0.266100      5863.555664       31.1   
3     ...  37.6450  127.022   45.7160  2.534800      5856.964844       31.7   
4     ...  37.5507  127.135   35.0380  0.505500      5859.552246       31.2   
...   ...      ...      ...       ...       ...              ...        ...   
7747  ...  37.5372  126.891   15.5876  0.155400      4443.313965       28.3   
7748  ...  37.5237  126.909   17.2956  0.222300      4438.373535       28.6   
7749  ...  37.5237  126.970   19.5844  0.271300      4451.345215       27.8   
7750  ...  37.4562  126.826   12.3700  0.098475      4329.520508       17.4   
7751  ...  37.6450  127.135  212.3350  5.178230      5992.895996       38.9   

      Next_Tmin    year  month   day  
0          21.2  2013.0    6.0  30.0  
1          22.5  2013.0    6.0  30.0  
2          23.9  2013.0    6.0  30.0  
3          24.3  2013.0    6.0  30.0  
4          22.5  2013.0    6.0  30.0  
...         ...     ...    ...   ...  
7747       18.1  2017.0    8.0  30.0  
7748       18.8  2017.0    8.0  30.0  
7749       17.4  2017.0    8.0  30.0  
7750       11.3     NaN    NaN   NaN  
7751       29.8     NaN    NaN   NaN  

[7752 rows x 27 columns]

In [16]:
temp.head()

station  Present_Tmax  Present_Tmin  LDAPS_RHmin  LDAPS_RHmax  \
0      1.0          28.7          21.4    58.255688    91.116364   
1      2.0          31.9          21.6    52.263397    90.604721   
2      3.0          31.6          23.3    48.690479    83.973587   
3      4.0          32.0          23.4    58.239788    96.483688   
4      5.0          31.4          21.9    56.174095    90.155128   

   LDAPS_Tmax_lapse  LDAPS_Tmin_lapse  LDAPS_WS    LDAPS_LH  LDAPS_CC1  ...  \
0         28.074101         23.006936  6.818887   69.451805   0.233947  ...   
1         29.850689         24.035009  5.691890   51.937448   0.225508  ...   
2         30.091292         24.565633  6.138224   20.573050   0.209344  ...   
3         29.704629         23.326177  5.650050   65.727144   0.216372  ...   
4         29.113934         23.486480  5.735004  107.965535   0.151407  ...   

       lat      lon       DEM   Slope  Solar radiation  Next_Tmax  Next_Tmin  \
0  37.6046  126.991  212.3350  2.7850      5992.895996       29.1       21.2   
1  37.6046  127.032   44.7624  0.5141      5869.312500       30.5       22.5   
2  37.5776  127.058   33.3068  0.2661      5863.555664       31.1       23.9   
3  37.6450  127.022   45.7160  2.5348      5856.964844       31.7       24.3   
4  37.5507  127.135   35.0380  0.5055      5859.552246       31.2       22.5   

     year  month   day  
0  2013.0    6.0  30.0  
1  2013.0    6.0  30.0  
2  2013.0    6.0  30.0  
3  2013.0    6.0  30.0  
4  2013.0    6.0  30.0  

[5 rows x 27 columns]

In [17]:
def plot_line(para):
    df = temp.groupby(by=para).mean().reset_index()

    plt.plot(df[para], df['Present_Tmax'], label='Present_Tmax', color="Red")
    plt.plot(df[para], df['Present_Tmin'], label='Present_Tmin', color="Yellow")
    plt.xlabel(para)
    plt.ylabel('Temperature')
    plt.legend()
    plt.grid(True)
    plt.title('Temperature Variation')
    plt.style.use('dark_background')
    plt.show()

In [18]:
plot_line('day')

In [19]:
def plot_line(para):
    df = temp.groupby(by=para).mean().reset_index()
    
    fig = px.line(df, x=df[para], y=['Present_Tmax', 'Present_Tmin'])
    #fig.update_layout(template='plotly_dark')
    return fig.show()

In [20]:
plot_line('day')

In [21]:
temp.columns

Index(['station', 'Present_Tmax', 'Present_Tmin', 'LDAPS_RHmin', 'LDAPS_RHmax',
       'LDAPS_Tmax_lapse', 'LDAPS_Tmin_lapse', 'LDAPS_WS', 'LDAPS_LH',
       'LDAPS_CC1', 'LDAPS_CC2', 'LDAPS_CC3', 'LDAPS_CC4', 'LDAPS_PPT1',
       'LDAPS_PPT2', 'LDAPS_PPT3', 'LDAPS_PPT4', 'lat', 'lon', 'DEM', 'Slope',
       'Solar radiation', 'Next_Tmax', 'Next_Tmin', 'year', 'month', 'day'],
      dtype='object')

In [22]:
temp.head()

station  Present_Tmax  Present_Tmin  LDAPS_RHmin  LDAPS_RHmax  \
0      1.0          28.7          21.4    58.255688    91.116364   
1      2.0          31.9          21.6    52.263397    90.604721   
2      3.0          31.6          23.3    48.690479    83.973587   
3      4.0          32.0          23.4    58.239788    96.483688   
4      5.0          31.4          21.9    56.174095    90.155128   

   LDAPS_Tmax_lapse  LDAPS_Tmin_lapse  LDAPS_WS    LDAPS_LH  LDAPS_CC1  ...  \
0         28.074101         23.006936  6.818887   69.451805   0.233947  ...   
1         29.850689         24.035009  5.691890   51.937448   0.225508  ...   
2         30.091292         24.565633  6.138224   20.573050   0.209344  ...   
3         29.704629         23.326177  5.650050   65.727144   0.216372  ...   
4         29.113934         23.486480  5.735004  107.965535   0.151407  ...   

       lat      lon       DEM   Slope  Solar radiation  Next_Tmax  Next_Tmin  \
0  37.6046  126.991  212.3350  2.7850      5992.895996       29.1       21.2   
1  37.6046  127.032   44.7624  0.5141      5869.312500       30.5       22.5   
2  37.5776  127.058   33.3068  0.2661      5863.555664       31.1       23.9   
3  37.6450  127.022   45.7160  2.5348      5856.964844       31.7       24.3   
4  37.5507  127.135   35.0380  0.5055      5859.552246       31.2       22.5   

     year  month   day  
0  2013.0    6.0  30.0  
1  2013.0    6.0  30.0  
2  2013.0    6.0  30.0  
3  2013.0    6.0  30.0  
4  2013.0    6.0  30.0  

[5 rows x 27 columns]

In [23]:
temp.drop('station', axis=1, inplace=True)

In [24]:
def treat_nan(df):
    df = df.fillna(df.mean())
    return df

In [25]:
treat_nan(temp)

Present_Tmax  Present_Tmin  LDAPS_RHmin  LDAPS_RHmax  LDAPS_Tmax_lapse  \
0             28.7          21.4    58.255688    91.116364         28.074101   
1             31.9          21.6    52.263397    90.604721         29.850689   
2             31.6          23.3    48.690479    83.973587         30.091292   
3             32.0          23.4    58.239788    96.483688         29.704629   
4             31.4          21.9    56.174095    90.155128         29.113934   
...            ...           ...          ...          ...               ...   
7747          23.3          17.1    26.741310    78.869858         26.352081   
7748          23.3          17.7    24.040634    77.294975         27.010193   
7749          23.2          17.4    22.933014    77.243744         27.939516   
7750          20.0          11.3    19.794666    58.936283         17.624954   
7751          37.6          29.9    98.524734   100.000153         38.542255   

      LDAPS_Tmin_lapse   LDAPS_WS    LDAPS_LH  LDAPS_CC1  LDAPS_CC2  ...  \
0            23.006936   6.818887   69.451805   0.233947   0.203896  ...   
1            24.035009   5.691890   51.937448   0.225508   0.251771  ...   
2            24.565633   6.138224   20.573050   0.209344   0.257469  ...   
3            23.326177   5.650050   65.727144   0.216372   0.226002  ...   
4            23.486480   5.735004  107.965535   0.151407   0.249995  ...   
...                ...        ...         ...        ...        ...  ...   
7747         18.775678   6.148918   72.058294   0.030034   0.081035  ...   
7748         18.733519   6.542819   47.241457   0.035874   0.074962  ...   
7749         18.522965   7.289264    9.090034   0.048954   0.059869  ...   
7750         14.272646   2.882580  -13.603212   0.000000   0.000000  ...   
7751         29.619342  21.857621  213.414006   0.967277   0.968353  ...   

          lat      lon       DEM     Slope  Solar radiation  Next_Tmax  \
0     37.6046  126.991  212.3350  2.785000      5992.895996       29.1   
1     37.6046  127.032   44.7624  0.514100      5869.312500       30.5   
2     37.5776  127.058   33.3068  0.266100      5863.555664       31.1   
3     37.6450  127.022   45.7160  2.534800      5856.964844       31.7   
4     37.5507  127.135   35.0380  0.505500      5859.552246       31.2   
...       ...      ...       ...       ...              ...        ...   
7747  37.5372  126.891   15.5876  0.155400      4443.313965       28.3   
7748  37.5237  126.909   17.2956  0.222300      4438.373535       28.6   
7749  37.5237  126.970   19.5844  0.271300      4451.345215       27.8   
7750  37.4562  126.826   12.3700  0.098475      4329.520508       17.4   
7751  37.6450  127.135  212.3350  5.178230      5992.895996       38.9   

      Next_Tmin    year     month        day  
0          21.2  2013.0  6.000000  30.000000  
1          22.5  2013.0  6.000000  30.000000  
2          23.9  2013.0  6.000000  30.000000  
3          24.3  2013.0  6.000000  30.000000  
4          22.5  2013.0  6.000000  30.000000  
...         ...     ...       ...        ...  
7747       18.1  2017.0  8.000000  30.000000  
7748       18.8  2017.0  8.000000  30.000000  
7749       17.4  2017.0  8.000000  30.000000  
7750       11.3  2015.0  7.467742  15.983871  
7751       29.8  2015.0  7.467742  15.983871  

[7752 rows x 26 columns]

In [26]:
temp.head()

Present_Tmax  Present_Tmin  LDAPS_RHmin  LDAPS_RHmax  LDAPS_Tmax_lapse  \
0          28.7          21.4    58.255688    91.116364         28.074101   
1          31.9          21.6    52.263397    90.604721         29.850689   
2          31.6          23.3    48.690479    83.973587         30.091292   
3          32.0          23.4    58.239788    96.483688         29.704629   
4          31.4          21.9    56.174095    90.155128         29.113934   

   LDAPS_Tmin_lapse  LDAPS_WS    LDAPS_LH  LDAPS_CC1  LDAPS_CC2  ...      lat  \
0         23.006936  6.818887   69.451805   0.233947   0.203896  ...  37.6046   
1         24.035009  5.691890   51.937448   0.225508   0.251771  ...  37.6046   
2         24.565633  6.138224   20.573050   0.209344   0.257469  ...  37.5776   
3         23.326177  5.650050   65.727144   0.216372   0.226002  ...  37.6450   
4         23.486480  5.735004  107.965535   0.151407   0.249995  ...  37.5507   

       lon       DEM   Slope  Solar radiation  Next_Tmax  Next_Tmin    year  \
0  126.991  212.3350  2.7850      5992.895996       29.1       21.2  2013.0   
1  127.032   44.7624  0.5141      5869.312500       30.5       22.5  2013.0   
2  127.058   33.3068  0.2661      5863.555664       31.1       23.9  2013.0   
3  127.022   45.7160  2.5348      5856.964844       31.7       24.3  2013.0   
4  127.135   35.0380  0.5055      5859.552246       31.2       22.5  2013.0   

   month   day  
0    6.0  30.0  
1    6.0  30.0  
2    6.0  30.0  
3    6.0  30.0  
4    6.0  30.0  

[5 rows x 26 columns]

In [27]:
X = temp.drop(['Next_Tmax', 'Next_Tmin'], axis=1)
y1 = temp['Next_Tmax']
y2 = temp['Next_Tmin']

In [28]:
X.head()

Present_Tmax  Present_Tmin  LDAPS_RHmin  LDAPS_RHmax  LDAPS_Tmax_lapse  \
0          28.7          21.4    58.255688    91.116364         28.074101   
1          31.9          21.6    52.263397    90.604721         29.850689   
2          31.6          23.3    48.690479    83.973587         30.091292   
3          32.0          23.4    58.239788    96.483688         29.704629   
4          31.4          21.9    56.174095    90.155128         29.113934   

   LDAPS_Tmin_lapse  LDAPS_WS    LDAPS_LH  LDAPS_CC1  LDAPS_CC2  ...  \
0         23.006936  6.818887   69.451805   0.233947   0.203896  ...   
1         24.035009  5.691890   51.937448   0.225508   0.251771  ...   
2         24.565633  6.138224   20.573050   0.209344   0.257469  ...   
3         23.326177  5.650050   65.727144   0.216372   0.226002  ...   
4         23.486480  5.735004  107.965535   0.151407   0.249995  ...   

   LDAPS_PPT3  LDAPS_PPT4      lat      lon       DEM   Slope  \
0         0.0         0.0  37.6046  126.991  212.3350  2.7850   
1         0.0         0.0  37.6046  127.032   44.7624  0.5141   
2         0.0         0.0  37.5776  127.058   33.3068  0.2661   
3         0.0         0.0  37.6450  127.022   45.7160  2.5348   
4         0.0         0.0  37.5507  127.135   35.0380  0.5055   

   Solar radiation    year  month   day  
0      5992.895996  2013.0    6.0  30.0  
1      5869.312500  2013.0    6.0  30.0  
2      5863.555664  2013.0    6.0  30.0  
3      5856.964844  2013.0    6.0  30.0  
4      5859.552246  2013.0    6.0  30.0  

[5 rows x 24 columns]

In [29]:
def normalizer(x_train, x_test):
    scaler = Normalizer()
    x_train = scaler.fit_transform(x_train)
    x_test = scaler.fit_transform(x_test)
    return x_train, x_test

In [30]:
def minmax(x_train, x_test):
    scaler = MinMaxScaler()
    x_train = scaler.fit_transform(x_train)
    x_test = scaler.fit_transform(x_test)
    return x_train, x_test

In [31]:
def stdscaler(x_train, x_test):
    scaler = StandardScaler()
    x_train = scaler.fit_transform(x_train)
    x_test = scaler.fit_transform(x_test)
    return x_train, x_test

In [32]:
def best_model(X, y, scaler, algo):
   
    df = pd.concat([X, y], axis=1)
    df = df.replace([np.inf, -np.inf], np.nan)
    df = df.dropna()

    X = df.iloc[:, :-1].values
    y = df.iloc[:, -1].values

    X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.25, random_state=42, shuffle=True)

    X_train = np.asarray(X_train)
    X_test = np.asarray(X_test)

    X_train, X_test = scaler(X_train, X_test)

    model = algo()

    model.fit(X_train, y_train)

    predictions = model.predict(X_test)

    mae = mean_absolute_error(predictions, y_test)
    mse = mean_squared_error(predictions, y_test)

    print(f'The MAE is {mae}')
    print(f'The MSE is {mse}')

    fig = px.scatter(x=predictions, y=y_test,  title='Actual Productivity vs Predictions')
    fig.update_traces(hovertemplate='Predicted Value : %{x} <br> Actual Value: %{y}')
    fig.update_layout(hoverlabel=dict(
        font_size=20,
        bgcolor='white',
        font_family='Helvetica'
    ))
    fig.update_xaxes(title='Predicted Values', showgrid=False)
    fig.update_yaxes(title='Actual Values', showgrid=False)

    return predictions, y_test, mse, mae, fig.show()



In [65]:
list_of_target = [y1, y2]

list_of_algos = [LinearRegression, KNeighborsRegressor, DecisionTreeRegressor, RandomForestRegressor, SVR]

list_of_MAE = []
list_of_MSE = []

for i in list_of_algos:
    print(f"{i}")
    pred, y_test, mse, mae, plot =best_model(X, y1, normalizer, i)
    list_of_MSE.append(mse)
    list_of_MAE.append(mae) 

<class 'sklearn.linear_model._base.LinearRegression'>
The MAE is 1.1060677621589647
The MSE is 2.1067514011924042


<class 'sklearn.neighbors._regression.KNeighborsRegressor'>
The MAE is 1.4776383763837637
The MSE is 3.7021566684238274


<class 'sklearn.tree._classes.DecisionTreeRegressor'>
The MAE is 1.018450184501845
The MSE is 2.082730627306273


<class 'sklearn.ensemble._forest.RandomForestRegressor'>
The MAE is 0.6777522403795466
The MSE is 0.8229416763310492


<class 'sklearn.svm._classes.SVR'>
The MAE is 2.4538453360288863
The MSE is 9.342606908443948


In [34]:
msemae_y1 = pd.DataFrame()
msemae_y1['Algos'] =  ['LinearRegression', 'KNeighborsRegressor', 'DecisionTreeRegressor', 'RandomForestRegressor', 'SVR']
msemae_y1['MSE_normalizer'] = list_of_MSE
msemae_y1['MAE_normalizer'] = list_of_MAE 

In [35]:
msemae_y1.head()

Algos  MSE_normalizer  MAE_normalizer
0       LinearRegression        2.106751        1.106068
1    KNeighborsRegressor        3.702157        1.477638
2  DecisionTreeRegressor        2.111534        1.021613
3  RandomForestRegressor        0.819516        0.679603
4                    SVR        9.342607        2.453845

In [66]:
list_of_MAE1 = []
list_of_MSE1 = []

for i in list_of_algos:
    print(f"{i}")
    pred, y_test, mse, mae, plot = best_model(X, y1, stdscaler, i)
    list_of_MSE1.append(mse)
    list_of_MAE1.append(mae)

<class 'sklearn.linear_model._base.LinearRegression'>
The MAE is 1.075032372767694
The MSE is 2.034922195487092


<class 'sklearn.neighbors._regression.KNeighborsRegressor'>
The MAE is 0.7643120716921455
The MSE is 1.0524683183974697


<class 'sklearn.tree._classes.DecisionTreeRegressor'>
The MAE is 1.084870848708487
The MSE is 2.264122298365841


<class 'sklearn.ensemble._forest.RandomForestRegressor'>
The MAE is 0.7211850289931468
The MSE is 0.9357351808118073


<class 'sklearn.svm._classes.SVR'>
The MAE is 0.770028443269004
The MSE is 1.1175508488848254


In [37]:
msemae_y1['MSE_stdscaler'] = list_of_MSE1
msemae_y1['MAE_stdscaler'] = list_of_MAE1 

In [67]:
list_of_MAE2 = []
list_of_MSE2 = []

for i in list_of_algos:
    print(f"{i}")
    pred, y_test, mse, mae, plot = best_model(X, y1, minmax, i)
    list_of_MSE2.append(mse)
    list_of_MAE2.append(mae)

<class 'sklearn.linear_model._base.LinearRegression'>
The MAE is 1.123999693015241
The MSE is 2.1931629071549064


<class 'sklearn.neighbors._regression.KNeighborsRegressor'>
The MAE is 0.8051449657353718
The MSE is 1.1848151818661046


<class 'sklearn.tree._classes.DecisionTreeRegressor'>
The MAE is 1.2359515023721666
The MSE is 2.8360674749604637


<class 'sklearn.ensemble._forest.RandomForestRegressor'>
The MAE is 0.8458381655245125
The MSE is 1.2826628439641539


<class 'sklearn.svm._classes.SVR'>
The MAE is 0.9222159445013216
The MSE is 1.5643850707894722


In [39]:
msemae_y1['MSE_minmax'] = list_of_MSE2
msemae_y1['MAE_minmax'] = list_of_MAE2 

In [40]:
msemae_y1.head()

Algos  MSE_normalizer  MAE_normalizer  MSE_stdscaler  \
0       LinearRegression        2.106751        1.106068       2.034922   
1    KNeighborsRegressor        3.702157        1.477638       1.052468   
2  DecisionTreeRegressor        2.111534        1.021613       2.257085   
3  RandomForestRegressor        0.819516        0.679603       0.907640   
4                    SVR        9.342607        2.453845       1.117551   

   MAE_stdscaler  MSE_minmax  MAE_minmax  
0       1.075032    2.193163    1.124000  
1       0.764312    1.184815    0.805145  
2       1.084291    2.870032    1.245177  
3       0.714987    1.261608    0.844033  
4       0.770028    1.564385    0.922216

In [61]:
list_of_algos = [LinearRegression, KNeighborsRegressor, DecisionTreeRegressor, RandomForestRegressor, SVR]

list_of_MAE3 = []
list_of_MSE3 = []

for i in list_of_algos:
    print(f"{i}")
    pred, y_test, mse, mae, plot = best_model(X, y2, normalizer, i)
    list_of_MSE3.append(mse)
    list_of_MAE3.append(mae)

<class 'sklearn.linear_model._base.LinearRegression'>
The MAE is 0.782677020003864
The MSE is 1.0146179688537629


<class 'sklearn.neighbors._regression.KNeighborsRegressor'>
The MAE is 1.2021929362150765
The MSE is 2.442863046916183


<class 'sklearn.tree._classes.DecisionTreeRegressor'>
The MAE is 0.804955192409067
The MSE is 1.2263995782814974


<class 'sklearn.ensemble._forest.RandomForestRegressor'>
The MAE is 0.5656104375329466
The MSE is 0.5665534175013174


<class 'sklearn.svm._classes.SVR'>
The MAE is 1.9115719588977664
The MSE is 5.8063216259294865


In [42]:
msemae_y2 = pd.DataFrame()
msemae_y2['Algos'] =  ['LinearRegression', 'KNeighborsRegressor', 'DecisionTreeRegressor', 'RandomForestRegressor', 'SVR']
msemae_y2['MSE_normalizer'] = list_of_MSE3
msemae_y2['MAE_normalizer'] = list_of_MAE3

In [62]:
list_of_MAE4 = []
list_of_MSE4 = []

for i in list_of_algos:
    print(f"{i}")
    pred, y_test, mse, mae, plot = best_model(X, y2, stdscaler, i)
    list_of_MSE4.append(mse)
    list_of_MAE4.append(mae)

<class 'sklearn.linear_model._base.LinearRegression'>
The MAE is 0.7722948948657591
The MSE is 0.997136538878165


<class 'sklearn.neighbors._regression.KNeighborsRegressor'>
The MAE is 0.6332630469161834
The MSE is 0.7014209804955193


<class 'sklearn.tree._classes.DecisionTreeRegressor'>
The MAE is 0.8652082235108065
The MSE is 1.3727622561939905


<class 'sklearn.ensemble._forest.RandomForestRegressor'>
The MAE is 0.5764428044280443
The MSE is 0.5875567633104901


<class 'sklearn.svm._classes.SVR'>
The MAE is 0.5666463198617461
The MSE is 0.5694870664380287


In [44]:
msemae_y2['MSE_stdscaler'] = list_of_MSE4
msemae_y2['MAE_stdscaler'] = list_of_MAE4

In [64]:
list_of_MAE5 = []
list_of_MSE5 = []

for i in list_of_algos:
    print(f"{i}")
    pred, y_test, mse, mae, plot = best_model(X, y2, minmax, i)
    list_of_MSE5.append(mse)
    list_of_MAE5.append(mae)

<class 'sklearn.linear_model._base.LinearRegression'>
The MAE is 0.8401416382980031
The MSE is 1.0992535474324614


<class 'sklearn.neighbors._regression.KNeighborsRegressor'>
The MAE is 0.6511122825513971
The MSE is 0.7402070637849236


<class 'sklearn.tree._classes.DecisionTreeRegressor'>
The MAE is 0.9693726937269374
The MSE is 1.6454665260938324


<class 'sklearn.ensemble._forest.RandomForestRegressor'>
The MAE is 0.6870732735898789
The MSE is 0.7670908845545598


<class 'sklearn.svm._classes.SVR'>
The MAE is 0.689396838325732
The MSE is 0.7774531727396714


In [46]:
msemae_y2['MSE_minmax'] = list_of_MSE5
msemae_y2['MAE_minmax'] = list_of_MAE5

In [47]:
msemae_y2.head()

Algos  MSE_normalizer  MAE_normalizer  MSE_stdscaler  \
0       LinearRegression        1.014618        0.782677       0.997137   
1    KNeighborsRegressor        2.442863        1.202193       0.701421   
2  DecisionTreeRegressor        1.264997        0.810016       1.355224   
3  RandomForestRegressor        0.568555        0.561833       0.595733   
4                    SVR        5.806322        1.911572       0.569487   

   MAE_stdscaler  MSE_minmax  MAE_minmax  
0       0.772295    1.099254    0.840142  
1       0.633263    0.740207    0.651112  
2       0.856510    1.637217    0.967001  
3       0.581005    0.765621    0.686775  
4       0.566646    0.777453    0.689397

In [48]:
msemae_y1.head()

Algos  MSE_normalizer  MAE_normalizer  MSE_stdscaler  \
0       LinearRegression        2.106751        1.106068       2.034922   
1    KNeighborsRegressor        3.702157        1.477638       1.052468   
2  DecisionTreeRegressor        2.111534        1.021613       2.257085   
3  RandomForestRegressor        0.819516        0.679603       0.907640   
4                    SVR        9.342607        2.453845       1.117551   

   MAE_stdscaler  MSE_minmax  MAE_minmax  
0       1.075032    2.193163    1.124000  
1       0.764312    1.184815    0.805145  
2       1.084291    2.870032    1.245177  
3       0.714987    1.261608    0.844033  
4       0.770028    1.564385    0.922216

In [49]:
fig = px.bar(msemae_y2,  x='Algos', y=[ 'MSE_minmax', 'MAE_minmax'], barmode='group')
fig.update_layout(title='Representation of MAE and MSE values of different Algorithms on the Next Min Temperature', hoverlabel=dict(
    font_size=20,
    font_family='Arial'
))
fig.update_traces(hovertemplate='%{x} : %{y}')
fig.show()

In [52]:
fig = px.bar(msemae_y1,  x='Algos', y=[ 'MSE_minmax', 'MAE_minmax'], barmode='group')
fig.update_layout(title='Representation of MAE and MSE values of different Algorithms on the Next Max Temperature', hoverlabel=dict(
    font_size=20,
    font_family='Arial'
))
fig.update_traces(hovertemplate='%{x} : %{y}')
fig.show()

# THANK YOU